In [ ]:
import tarfile
import io
import zipfile
import importlib
import regex as re
import pyperclip  
import TexSoup as TS
from TexSoup.tokens import MATH_ENV_NAMES
import os

def find_doc_class(fp, name_match=False):
    '''Search for document class related lines in a file and return a code to represent the type'''
    doc_class_pat = re.compile(r"^\s*\\document(?:style|class)")
    sub_doc_class = re.compile(r"^\s*\\document(?:style|class).*(?:\{standalone\}|\{subfiles\})")

    # Read the content as bytes
    file_content = fp.read()
    try:
        # Try decoding with UTF-8
        file_text = file_content.decode('utf-8')
    except UnicodeDecodeError:
        # Fallback to latin-1 encoding if UTF-8 fails
        file_text = file_content.decode('latin-1')

    for line in file_text.splitlines():
        if doc_class_pat.search(line):
            if name_match:
                if sub_doc_class.search(line):
                    return -99999
                return 1  # Found document class line
    return 0  # No document class line found

def find_main_tex_source_in_tar(tar_file, encoding='utf-8'):
    tex_names = set(["paper", "main", "ms.", "article"])
    tex_files = [f for f in tar_file.getnames() if f.endswith('.tex')]

    if len(tex_files) == 1:
        return tex_files[0]

    main_files = {}
    for tf in tex_files:
        depth = len(tf.split('/')) - 1
        has_main_name = any(kw in tf for kw in tex_names)
        fp = tar_file.extractfile(tf)
        if fp:
            main_files[tf] = find_doc_class(fp, name_match=has_main_name) - depth
            fp.close()

    return max(main_files, key=main_files.get) if main_files else None

def pre_format(text):
    source_text = text.replace('\\}\\', '\\} \\').replace(')}', ') }').replace(')$', ') $')
    return source_text

def source_from_tar(tar_file, encoding='utf-8'):
    tex_main = find_main_tex_source_in_tar(tar_file, encoding=encoding)
    if tex_main:
        fp = tar_file.extractfile(tex_main)
        if fp is not None:
            file_content = fp.read()  # Read as bytes to keep it in memory
            try:
                # Attempt to decode using UTF-8
                source_text = pre_format(file_content.decode(encoding))
            except UnicodeDecodeError:
                # Fallback to latin-1 encoding if UTF-8 fails
                source_text = pre_format(file_content.decode('latin-1'))
            return source_text
    return None



def extract_before_abstract(source_text):
    no_comments_text = re.sub(r'(?<!\\)%.*', '', source_text)
    no_usepackage_text = re.sub(r'\\usepackage\s*\{[^}]+\}', '', no_comments_text)
    text = re.sub(r'\\[a-zA-Z]+\{[^}]*\}', '', no_usepackage_text)
    text = re.sub(r'\\[a-zA-Z]+\[[^\]]*\]\{[^}]*\}', '', no_usepackage_text)
    text = re.sub(r'\$[^$]*\$', '', no_usepackage_text)
    text = no_usepackage_text.replace('{', '').replace('}', '').replace('\n', ' ')
    text = ' '.join(no_usepackage_text.split())
    abstract_match = re.search(r'\\begin\s*\{\s*abstract\s*\}', text)

    if abstract_match:
        return text[:abstract_match.start()].strip()
    
    abstract_word_match = re.search(r'\babstract\b', text, re.IGNORECASE)
    if abstract_word_match:
        return text[:abstract_word_match.start()].strip()
    return None

zip_file_path = "./2401.zip"

with zipfile.ZipFile(zip_file_path, 'r') as zip_file:
    tar_files = [f for f in zip_file.namelist() if f.endswith('.tar.gz')]

    for tar_name in tar_files:
        with zip_file.open(tar_name) as tar_bytes:
            tar_file = tarfile.open(fileobj=io.BytesIO(tar_bytes.read()), mode='r:gz')
            source_text = source_from_tar(tar_file)
            if source_text:
                pyperclip.copy(source_text)
                content_before_abstract = extract_before_abstract(source_text)
                if content_before_abstract:
                    print(f"Content before abstract in {tar_name}:\n{content_before_abstract}\n")
                else:
                    print(f"No abstract found in {tar_name}, or no content before abstract.\n")
            tar_file.close()


Content before abstract in 2401/2401.00006v1.tar.gz:
\documentclass{article} \newcommand{\theHalgorithm}{\arabic{algorithm}} \usepackage[accepted]{icml2024} \usepackage[capitalize,noabbrev]{cleveref} \theoremstyle{plain} \newtheorem{theorem}{Theorem}[section] \newtheorem{proposition}[theorem]{Proposition} \newtheorem{lemma}[theorem]{Lemma} \newtheorem{corollary}[theorem]{Corollary} \theoremstyle{definition} \newtheorem{definition}[theorem]{Definition} \newtheorem{assumption}[theorem]{Assumption} \theoremstyle{remark} \newtheorem{remark}[theorem]{Remark} \usepackage[textsize=tiny]{todonotes} \usepackage[bb=boondox]{mathalfa} \usepackage[T1]{fontenc} \usepackage[normalem]{ulem} \useunder{\uline}{\ul}{} \newcommand{\fix}{\marginpar{FIX}} \newcommand{\new}{\marginpar{NEW}} \newcommand{\framework}{OpenContra} \newcommand{\Contra}{Contra} \newcommand{\bfemph}[1]{\textbf{\textit{#1}}} \newcommand{\ming}[1]{{\bf \color{orange} [[Ming says ``#1'']]}} \newcommand{\qi}[1]{{\bf \color{blue} [[Qi s

In [ ]:
# Read input from a text file and filter out files without valid content before the abstract
input_file_path = 'input.txt'  # Replace with your actual file path
output_file_path = 'filtered_files_with_content.txt'

# Variables to keep track of statistics
total_files_count_author = 0
valid_files_count = 0
valid_files_with_content = []

# Reading and processing the input file
with open(input_file_path, 'r') as infile:
    content_blocks = infile.read().split('Content before abstract in ')
    
    for block in content_blocks:
        if block.strip():  # Ensure we are not processing an empty block
            total_files_count_author += 1
            lines = block.split('\n', 1)  # Split to separate the file name from its content
            if len(lines) > 1:
                file_name = lines[0].strip().replace(':', '')
                content = lines[1].strip()
                
                # Check if the content does not indicate "No abstract found"
                if 'No abstract found' not in content and 'no content before abstract' not in content.lower():
                    valid_files_count += 1
                    valid_files_with_content.append((file_name, content))

# Writing the filtered results to an output file
with open(output_file_path, 'w') as outfile:
    for file_name, content in valid_files_with_content:
        outfile.write(f"Content before abstract in {file_name}:\n{content}\n\n")

# Print or save the statistics summary
# print(f"Total number of files processed: {total_files_count}")
# print(f"Total number of files with valid content before abstract: {valid_files_count}")
# print(f"Filtered output saved in: {output_file_path}")


2184

2240

855

497

908

...

723

917

2382

4721

1817

In [32]:
# Define the input and output file paths
input_file_path = 'filtered_files_with_content.txt'
output_file_path = 'filtered_without_tags.txt'

# Tags to search for and their counters
tags_to_search = [r'\\affiliations', r'\\affiliation', r'\\icmlaffiliation',  r'\\institute', r'\\affil', r'\\aff', r'\\AFF',r'\\address']
tag_counts = {tag: 0 for tag in tags_to_search}

# Helper function to check and remove content with specified tags
def contains_and_remove_tags(content, tags):
    for tag in tags:
        if re.search(tag, content):
            tag_counts[tag] += 1
            return True  # Stop at the first match and remove the paper's content
    return False

# Process the input and create the new output without specified tags
total_files_count = 0
files_kept_count = 0
files_without_tags = []

with open(input_file_path, 'r') as infile:
    content_blocks = infile.read().split('Content before abstract in ')

    for block in content_blocks:
        if block.strip():  # Ensure we are not processing an empty block
            total_files_count += 1
            lines = block.split('\n', 1)
            if len(lines) > 1:
                file_name = lines[0].strip().replace(':', '')
                content = lines[1].strip()

                # Check if the content includes any of the tags and remove if found
                if not contains_and_remove_tags(content, tags_to_search):
                    files_kept_count += 1
                    files_without_tags.append(f"Content before abstract in {file_name}:\n{content}\n")

# Write the filtered content to the output file
with open(output_file_path, 'w') as outfile:
    outfile.write('\n'.join(files_without_tags))

# Print statistics
print(f"Total number of files processed: {total_files_count}")
for tag, count in tag_counts.items():
    print(f"Number of papers with tag '{tag}': {count}")
print(f"Total number of files kept after filtering: {files_kept_count}")
print(f"Filtered output saved in: {output_file_path}")


1717501

Total number of files processed: 2134
Number of papers with tag '\\affiliations': 107
Number of papers with tag '\\affiliation': 593
Number of papers with tag '\\icmlaffiliation': 54
Number of papers with tag '\\institute': 107
Number of papers with tag '\\affil': 125
Number of papers with tag '\\aff': 7
Number of papers with tag '\\AFF': 7
Number of papers with tag '\\address': 204
Total number of files kept after filtering: 930
Filtered output saved in: filtered_without_tags.txt


In [33]:
import re

# Define the input and output file paths
input_file_path = 'filtered_without_tags.txt'
output_file_path = 'filtered_without_authors.txt'

# Counter for the number of filtered and kept files
total_files_count_author = 0
filtered_files_count = 0
kept_files_count = 0

# Function to check if the content has an \author{} tag with line breaks
def contains_author_with_line_break(content):
    author_tag_pattern = re.compile(r'\\author\s*{.*?\\.*?}', re.S)
    return bool(author_tag_pattern.search(content))

# List to store files without the filtered \author{} tag content
files_without_author_tag = []

# Read the input file and process each content block
with open(input_file_path, 'r') as infile:
    content_blocks = infile.read().split('Content before abstract in ')

    for block in content_blocks:
        if block.strip():  # Ensure we are not processing an empty block
            total_files_count_author += 1
            lines = block.split('\n', 1)
            if len(lines) > 1:
                file_name = lines[0].strip().replace(':', '')
                content = lines[1].strip()

                # Check if the content has \author{} with \\ line breaks
                if contains_author_with_line_break(content):
                    filtered_files_count += 1
                else:
                    kept_files_count += 1
                    files_without_author_tag.append(f"Content before abstract in {file_name}:\n{content}\n")

# Write the filtered content to the output file
with open(output_file_path, 'w') as outfile:
    outfile.write('\n'.join(files_without_author_tag))

# Print statistics
print(f"Total number of files processed: {total_files_count}")
for tag, count in tag_counts.items():
    print(f"Number of papers with tag '{tag}': {count}")
# print(f"Total number of files processed: {total_files_count_author}")
print(f"Number of files with \\author{{}} containing line breaks: {filtered_files_count}")
print(f"Total number of files kept after filtering: {kept_files_count}")
print(f"Filtered output saved in: {output_file_path}")


308880

Total number of files processed: 2134
Number of papers with tag '\\affiliations': 107
Number of papers with tag '\\affiliation': 593
Number of papers with tag '\\icmlaffiliation': 54
Number of papers with tag '\\institute': 107
Number of papers with tag '\\affil': 125
Number of papers with tag '\\aff': 7
Number of papers with tag '\\AFF': 7
Number of papers with tag '\\address': 204
Number of files with \author{} containing line breaks: 786
Total number of files kept after filtering: 144
Filtered output saved in: filtered_without_authors.txt


Total number of files processed: 2134
Number of papers with tag '\affiliations': 107 (5%)
Number of papers with tag '\\affiliation': 593 (28%)
Number of papers with tag '\\icmlaffiliation': 54 (2.5%)
Number of papers with tag '\\institute': 107 (5%)
Number of papers with tag '\\affil': 125 (6%)
Number of papers with tag '\\aff': 7 (0.3%)
Number of papers with tag '\\AFF': 7 (0.3%)
Number of papers with tag '\\address': 204 (10%)
Number of files with \author{} containing line breaks: 786 (36%)
-- 1763 / 2134 (83%) paper used those tags for affiliation info --- 
Total number of files kept after filtering: 144 (7%)


\ARTICLEAUTHORS
\thanks

In [ ]:
from typing import List, Tuple

def find_destination(height_map: List[List[int]], start_row: int, start_col: int) -> Tuple[int, int]:
    rows, cols = len(height_map), len(height_map[0])
    memo = {}  # Memoization table to store destinations for each cell

    def dfs(row: int, col: int) -> Tuple[int, int]:
        # If we have already computed the destination for this cell, return it
        if (row, col) in memo:
            return memo[(row, col)]
        
        # Initialize the current cell as the destination
        destination = (row, col)
        min_height = height_map[row][col]

        # Define directions: up, down, left, right
        directions = [(-1, 0), (1, 0), (0, -1), (0, 1)]

        # Explore each direction
        for dr, dc in directions:
            new_row, new_col = row + dr, col + dc
            if 0 <= new_row < rows and 0 <= new_col < cols:
                if height_map[new_row][new_col] < min_height:
                    # Recurse to the lower height cell
                    dest = dfs(new_row, new_col)
                    destination = dest
                    min_height = height_map[new_row][new_col]
        
        # Store result in memo
        memo[(row, col)] = destination
        return destination

    # Start DFS from the specified start cell
    return dfs(start_row, start_col)
